# Structured Streaming from kafka topic

In [ ]:
flume-ng agent --conf conf --conf-file /usr/local/Cellar/flume/1.9.0/libexec/conf/flume-sample.conf  -Dflume.root.logger=DEBUG,console --name a1 -Xmx512m -Xms256m

In [ ]:
!flume-ng agent --conf conf --conf-file /Users/val/Documents/code/spark/m11_to_Upload/netcat.conf.txt  -Dflume.root.logger=DEBUG,console --name NetcatAgent -Xmx512m -Xms256m

In [1]:
import os
def get_hdfs_filepath(file_name, on_cloud=False):
    # path to folder containing this code
    prefix = '/data/spark/11_cs1_dataset_stream/'
    if on_cloud:
        bucket  = os.environ['BUCKET']
        file_path = bucket + prefix + file_name
    else:
        file_path = '/Users/val' + prefix + file_name

    return file_path

In [2]:
import os
os.environ['PYSPARK_SUBMIT_ARGS'] = '--packages org.apache.spark:spark-sql-kafka-0-10_2.11:2.4.3 pyspark-shell'

import pyspark
import sys

from pyspark import SparkConf,SparkContext
from pyspark.streaming import StreamingContext

from pyspark.streaming.kafka import KafkaUtils


from pyspark.context import SparkContext
from pyspark.sql.session import SparkSession
sc = SparkContext("local[2]", "Streaming_Linear_Regression")
spark = SparkSession(sc)





In [3]:
# Subscribe to 1 topic
#df = spark \
#    .readStream \
#    .format("kafka") \
#    .option("kafka.bootstrap.servers", "localhost:9092") \
#    .option("subscribe", "sample-topic") \
#    .option("startingOffsets", "earliest") \
#    .load()

#df = df.selectExpr( "CAST(value AS STRING)")


#import pyspark.sql.functions as f
# split text lines into two fields
#split_col = f.split(df['value'], '\t')
#df = df.withColumn('spam', split_col.getItem(0))
#df = df.withColumn('message', split_col.getItem(1))
#df = df.select(['spam', 'message'])

# convert label: spam = 1, ham = 0 
#from pyspark.sql import functions as f
#df = df.withColumn("label", f.when(f.col('spam') == "spam", 1).otherwise(0))

In [5]:
from pyspark.sql.types import StructType
from pyspark.sql import functions as f

cwd = os.getcwd()
# screen subfolders in working directory for new csv files
userSchema = StructType().add("spam", "string").add("message", "string")
df = spark \
    .readStream \
    .option("sep", "\t") \
    .schema(userSchema)  \
    .csv(cwd+"/"+"module11_cs1/train_data_csv")     # Equivalent to format("csv").load("/path/to/directory")
df_test = spark \
    .readStream \
    .option("sep", "\t") \
    .schema(userSchema)  \
    .csv(cwd+"/"+"module11_cs1/test_data_csv")     # Equivalent to format("csv").load("/path/to/directory")


############################################
# convert label: spam = 1, ham = 0
df = df.withColumn("label", f.when(f.col('spam') == "spam", 1).otherwise(0))
df_test = df_test.withColumn("label", f.when(f.col('spam') == "spam", 1).otherwise(0))

In [6]:
from pyspark.ml import Pipeline, PipelineModel

from pyspark.ml.feature import Tokenizer
from pyspark.ml.feature import StopWordsRemover
from pyspark.ml.feature import HashingTF

# Extract words
tokenizer = Tokenizer().setInputCol("message").setOutputCol("words")
# Remove stopwords
# custom stopwords
stopwords = StopWordsRemover().getStopWords() + ["-"]
remover = StopWordsRemover().setStopWords(stopwords).setInputCol("words").setOutputCol("filtered")
# create features
hashingTF = HashingTF(numFeatures=10, inputCol="words", outputCol="features")

pipeline = Pipeline().setStages([tokenizer, remover, hashingTF])



In [7]:
featured = pipeline.fit(df).transform(df)
featured_test = pipeline.fit(df_test).transform(df_test)

In [8]:
#featured.writeStream.format("console").start()

In [9]:

import json
from pyspark.mllib.linalg import Vectors, SparseVector, DenseVector

from pyspark.mllib.linalg import Vectors
from pyspark.mllib.regression import LabeledPoint
from pyspark.mllib.regression import StreamingLinearRegressionWithSGD

def parse_json_line(line):
    label = (json.loads(line))['label']
    feat_vec = (json.loads(line))['features']
    vec = Vectors.sparse(feat_vec['size'], feat_vec['indices'], feat_vec['values'])
    return LabeledPoint(label, vec)



ssc = StreamingContext(sc, 1)
# get Dstream from json files in monitored dir for training
trainingData = ssc.textFileStream(get_hdfs_filepath(file_name="train_stream_json/")).map(parse_json_line).cache()
trainingData.pprint()

# get Dstream from json files in monitored dir for prediction
testData = ssc.textFileStream(get_hdfs_filepath(file_name="test_stream_json/")).map(parse_json_line)
testData.pprint()

numFeatures = 10

# initialize a model 
model = StreamingLinearRegressionWithSGD()
model.setInitialWeights([0.0, 0.0, 0.0, 0.0, 0.0, 0.0,0.0, 0.0, 0.0, 0.0])
# train the model on Dstream 
model.trainOn(trainingData)

# print predictions to the console
model.predictOnValues(testData.map(lambda lp: (lp.label, lp.features))).pprint()

ssc.start()
 
pass

In [10]:
featured['label','features'].writeStream \
    .format("json") \
    .option("path", get_hdfs_filepath(file_name="train_stream_json")) \
    .option("checkpointLocation", get_hdfs_filepath(file_name="chkpnt1"))\
    .start()

featured_test['label','features'].writeStream \
    .format("json") \
    .option("path", get_hdfs_filepath(file_name="test_stream_json/")) \
    .option("checkpointLocation", get_hdfs_filepath(file_name="chkpnt2"))\
    .start()

-------------------------------------------
Time: 2020-01-13 10:11:32
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:32
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:32
-------------------------------------------



-------------------------------------------
Time: 2020-01-13 10:11:33
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:33
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:33
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:34
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:34
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:34
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:35
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:35
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:35
----------

-------------------------------------------
Time: 2020-01-13 10:11:55
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:55
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:55
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:56
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:56
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:56
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:57
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:57
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:11:57
----------

-------------------------------------------
Time: 2020-01-13 10:12:19
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:19
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:19
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:20
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:20
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:20
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:21
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:21
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:21
----------

-------------------------------------------
Time: 2020-01-13 10:12:43
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:43
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:43
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:44
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:44
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:44
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:45
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:45
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 10:12:45
----------

...

-------------------------------------------
Time: 2020-01-13 15:36:16
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:16
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:16
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:17
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:17
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:17
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:18
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:18
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:18
----------

-------------------------------------------
Time: 2020-01-13 15:36:40
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:40
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:40
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:41
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:41
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:41
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:42
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:42
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:36:42
----------

-------------------------------------------
Time: 2020-01-13 15:37:04
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:04
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:04
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:05
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:05
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:05
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:06
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:06
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:06
----------

-------------------------------------------
Time: 2020-01-13 15:37:28
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:28
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:28
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:29
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:29
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:29
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:30
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:30
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:30
----------

-------------------------------------------
Time: 2020-01-13 15:37:52
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:52
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:52
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:53
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:53
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:53
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:54
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:54
-------------------------------------------

-------------------------------------------
Time: 2020-01-13 15:37:54
----------

In [9]:
raw1.printSchema()

-------------------------------------------
Time: 2020-01-10 16:02:22
-------------------------------------------

root
 |-- features: struct (nullable = true)
 |    |-- indices: array (nullable = true)
 |    |    |-- element: long (containsNull = true)
 |    |-- size: long (nullable = true)
 |    |-- type: long (nullable = true)
 |    |-- values: array (nullable = true)
 |    |    |-- element: double (containsNull = true)
 |-- label: long (nullable = true)

-------------------------------------------
Time: 2020-01-10 16:02:23
-------------------------------------------

-------------------------------------------
Time: 2020-01-10 16:02:24
-------------------------------------------

-------------------------------------------
Time: 2020-01-10 16:02:25
-------------------------------------------



In [8]:
cwd = os.getcwd()
print(cwd)

/Users/val/Documents/code/spark


In [6]:
ssc.stop()

In [5]:
ssc.start()
ssc.awaitTermination()

NameError: name 'ssc' is not defined